In [ ]:
!pip install bert-extractive-summarizer

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 106.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 27.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 122.2 MB/s eta 0:00:00


In [ ]:
from summarizer import Summarizer
import torch
import math
from tqdm import tqdm

In [ ]:
def flatten(nested_list):
    return [item for sublist in nested_list for item in sublist]

In [ ]:
import torch
import sys
print('__Python VERSION:', sys.version)
print('__pyTorch VERSION:', torch.__version__)
print('__CUDA VERSION')
from subprocess import call
# call(["nvcc", "--version"]) does not work
["nvcc", "--version"]
print('__CUDNN VERSION:', torch.backends.cudnn.version())
print('__Number CUDA Devices:', torch.cuda.device_count())
print('__Devices')
call(["nvidia-smi", "--format=csv", "--query-gpu=index,name,driver_version,memory.total,memory.used,memory.free"])
print('Active CUDA Device: GPU', torch.cuda.current_device())
print ('Available devices ', torch.cuda.device_count())
print ('Current cuda device ', torch.cuda.current_device())

__Python VERSION: 3.10.11 (main, Apr  5 2023, 14:15:10) [GCC 9.4.0]
__pyTorch VERSION: 2.0.0+cu118
__CUDA VERSION
__CUDNN VERSION: 8700
__Number CUDA Devices: 1
__Devices
Active CUDA Device: GPU 0
Available devices  1
Current cuda device  0


In [ ]:
import math
from summarizer import Summarizer
from tqdm import tqdm

# summarize text using bertSum
def summarize_text(paper: str, ratio: float = 0.75, num_sentences_ratio: float = 0.1):
    # Use GPU if available
    if torch.cuda.is_available():
        device = torch.device("cuda")
        print("Running on GPU")
    else:
        device = torch.device("cpu")
        print("Running on CPU")

    model = Summarizer(gpu_id=0)
    
    section_series = paper["sections"]
    section_arr = section_series.values

    def avg_words(sentenceArr):
        total_tokens = 0
        for string in sentenceArr:
            tokens = string.split()  # Split the string into tokens by whitespace
            total_tokens += len(tokens)
     

        # Calculate the average number of tokens per string
        average_tokens = total_tokens / len(sentenceArr)
        return average_tokens


    sentences = []
    # Add progress bar with tqdm
    for section in tqdm(section_arr, desc="Processing sections"):
        sentences.extend(flatten(section))
    avg_sentenceLen = avg_words(sentences)
    sentences = ' '.join(sentences)
    #avg_setece_legth
    # num_sentences = math.ceil(num_sentences_ratio * len(sentences))
    num_sentences = math.ceil(2000 / avg_sentenceLen)
    print(num_sentences)
    result = model(sentences, num_sentences=num_sentences)

  
    return [result]

In [ ]:
import pandas as pd
from zipfile import ZipFile

# Load dataset
def loadDataset(path, fileName):
  zip_file = ZipFile(path)
  return pd.read_json(zip_file.open(fileName))

In [ ]:
import json
import os
import pickle
import glob

In [ ]:
def most_recent_pickle_index(save_folder_path):
  filenames = os.listdir(save_folder_path)

  # Filter filenames that match the pattern "checkpoint_{index}.pkl"
  filtered_filenames = [filename for filename in filenames if filename.startswith('checkpoint_') and filename.endswith('.pkl')]

  # Extract the indices from the filenames and convert them to integers
  indices = [int(filename.split('_')[1].split('.')[0]) for filename in filtered_filenames]

  # Check if there are any filenames
  if indices:
      # Find the filename with the highest index
      return max(indices)
  else:
      return None

In [ ]:
def summarize_with_checkpoint(path, JSONfileName, summary_function, nameOfYourSummary, save_folder_path, **kwargs):
  '''
  path: path to original dataset
  JSONfileName: name of original dataset
  summary_function: takes a (1, n) row of the original dataset as input, returns a summary string
  nameOfYourSummary: the name to save the new summary under in the final dataframe
  

  '''
  recent_index = most_recent_pickle_index(save_folder_path)
  print(f'recent index is {recent_index}')
  recent_path = f'{save_folder_path}checkpoint_{recent_index}.pkl'
  
  original_dataset = loadDataset(path, JSONfileName)

  if recent_index == None:
    #first time in:
    our_summary = pd.DataFrame()
    #set up the correct colums
    cols_to_copy = ['id', 'year', 'title', 'abstract', 'summary', 'keywords']
    for col_name in cols_to_copy:
      our_summary[col_name] = ''
    our_summary[nameOfYourSummary] = ''
    recent_index = -1
  
  else:
    our_summary = pd.read_pickle(recent_path)

  for index, row in original_dataset.iloc[recent_index+1:].iterrows():
    paper = pd.Series(row).copy().to_frame().T
    generated_summary = summary_function(paper, **kwargs)
    print(generated_summary)
    paper[nameOfYourSummary] = [generated_summary]


    #our_summary = our_summary.append(paper)
    our_summary = pd.concat([our_summary, paper])

    # Save pickle every 500 papers
    if index % 40 == 0:
        print(f"pickling index {index}")
        our_summary.to_pickle(f'{save_folder_path}checkpoint_{index}.pkl')

    if index > 1200:
      break
  # return our_summary

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
summarize_with_checkpoint(path = '/content/drive/MyDrive/Colab Notebooks/elife.zip', JSONfileName = 'train.json', summary_function = summarize_text, nameOfYourSummary = 'bertSum_text', save_folder_path = '/content/drive/MyDrive/pickles_bertSum', ratio = 0.75, num_sentences_ratio = 0.1)

recent index is None
Running on GPU


Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Processing sections: 100%|██████████| 1/1 [00:00<00:00, 829.73it/s]


51


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


...

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


['Live dynamics data in intact nervous systems are critical to understand developmental processes and mutant phenotypes during the establishment of synaptic connectivity . 2011;\xa0Clandinin and Feldheim , 2009; Feller and Sun , 2011 ) . The fly’s compound eye is an assembly of ~750 ommatidia . 2011; Feller and Sun , 2011;\xa0Ting , et al . , 2014 ) and over long periods at low resolution and with slow time lapse ( Rabinovich et al . , 2008 ) in an imaging chamber ( Figure 1b; detailed description in Online Methods and Figure 1—figure supplement 1 ) . Development of Drosophila pupal brains in an imaging chamber . ( b ) Ex vivo imaging chamber , top ( left ) and side ( right ) views ( see Figure 1—figure supplement 1 for step-by-step assembly ) . ( c-h ) Changes in brain morphology during development ex vivo v . Note that for the ex vivo brains , images of the same specimens were taken at different time points , while for the in vivo controls different brains had to be fixed and imaged 

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Processing sections: 100%|██████████| 1/1 [00:00<00:00, 1687.85it/s]


75


KeyboardInterrupt: ignored

In [ ]:
# summarize_with_checkpoint(path = 'elife.zip', JSONfileName = 'train.json',  summary_function = summarize_text, nameOfYourSummary = 'bertSum_text', save_folder_path = '/content/pickles2/', ratio = 0.8, num_sentences_ratio = 0.1)

In [ ]:
def dumpLastPklToJson(path, jsonFileName, jsonFileStoringPath):
    # Get list of all pkl files in the directory
    pkl_files = glob.glob(os.path.join(path, 'pickles_bertSumcheckpoint_*.pkl'))

    # If there are no pkl files, return
    if not pkl_files:
        print("No pkl files found")
        return

    # Sort the files by modification time
    pkl_files.sort(key=os.path.getmtime)

    # Get the latest file
    latest_pkl_file = pkl_files[-1]

    # Load data from the latest pkl file
    with open(latest_pkl_file, 'rb') as f:
        data = pickle.load(f)

    # Dump data to JSON file
    json_file_path = os.path.join(jsonFileStoringPath, jsonFileName)
    if isinstance(data, pd.DataFrame):
        # If data is a DataFrame, use pandas' to_json() method
        data.to_json(json_file_path, orient="records", lines=True)
    else:
        # If data is not a DataFrame, use the json module
        with open(json_file_path, 'w') as f:
            json.dump(data, f, indent=4)

    print(f"Data from {latest_pkl_file} has been dumped to {json_file_path}")


In [ ]:
dumpLastPklToJson("/content/drive/MyDrive/", "realBertSum_train-720.json", "/content")

Data from /content/drive/MyDrive/pickles_bertSumcheckpoint_720.pkl has been dumped to /content/realBertSum_train-720.json


In [ ]:
data = []
with open('/content/realBertSum_test.json') as f:
    for line in f:
        data.append(json.loads(line))

dataF = pd.DataFrame(data)
dataFMySummary = dataF["bertSum_text"]

In [ ]:
dataF

id  year                                              title  \
0    elife-35500-v1  2018  National and regional seasonal dynamics of all...   
1    elife-48378-v2  2019  Complement and CD4+ T cells drive context-spec...   
2    elife-04494-v1  2015  Phenotypic complementation of genetic immunode...   
3    elife-12352-v2  2016  Cascade of neural processing orchestrates cogn...   
4    elife-05413-v2  2015  Structural dynamics of myosin 5 during process...   
..              ...   ...                                                ...   
746  elife-06564-v1  2015  Rapid categorization of natural face images in...   
747  elife-20383-v2  2017  Structure of the malaria vaccine candidate ant...   
748  elife-52651-v2  2020  Altered corticolimbic connectivity reveals sex...   
749  elife-27237-v1  2017  Localised dynactin protects growing microtubul...   
750  elife-48507-v3  2019  Fgf-signaling is compartmentalized within the ...   

                                              abstract  \
0    [In temperate climates , winter deaths exceed ...   
1    [Whether complement dysregulation directly con...   
2    [Variation in the presentation of hereditary i...   
3    [Rapid and flexible interpretation of conflict...   
4    [Myosin 5a is a dual-headed molecular motor th...   
..                                                 ...   
746  [Human performance at categorizing natural vis...   
747  [Invasion of erythrocytes by Plasmodial merozo...   
748  [Exposure to early-life adversity ( ELA ) incr...   
749  [The localisation of oskar mRNA to the posteri...   
750  [Although decades of studies have produced a g...   

                                               summary  \
0    [In the USA , more deaths happen in the winter...   
1    [Most people have likely experienced the disco...   
2    [The immune system protects an individual from...   
3    [The brain adapts to control our behavior in d...   
4    [Cells use motor proteins that to move organel...   
..                                                 ...   
746  [Putting names to faces can sometimes be chall...   
747  [Malaria is one of the deadliest infectious di...   
748  [Having a traumatic childhood increases the ri...   
749  [Many cells are asymmetric or polarized , whic...   
750  [Salamanders are a group of amphibians that ar...   

                                              keywords  \
0                     [epidemiology and global health]   
1    [microbiology and infectious disease, immunolo...   
2    [microbiology and infectious disease, immunolo...   
3                                       [neuroscience]   
4        [structural biology and molecular biophysics]   
..                                                 ...   
746                                     [neuroscience]   
747  [structural biology and molecular biophysics, ...   
748              [developmental biology, neuroscience]   
749                                     [cell biology]   
750      [developmental biology, evolutionary biology]   

                                          bertSum_text  \
0    [It is well-established that death rates vary ...   
1    [Dysregulated complement activation is increas...   
2    [HOIL-1 ( encoded by the RBCK1 gene ) , HOIP (...   
3    [Flexible control of cognitive processes is fu...   
4    [Myosin 5a moves in a hand-over-hand fashion w...   
..                                                 ...   
746  [A fundamental function of the human brain is ...   
747  [According to the World Health Organization 20...   
748  [Exposure to early life adversity ( ELA ) incr...   
749  [Although most tissue culture cells organise a...   
750  [Limb development is an ideal model to investi...   

                                              sections  \
0    [[It is well-established that death rates vary...   
1    [[Dysregulated complement activation is increa...   
2    [[HOIL-1 ( encoded by the RBCK1 gene ) , HOIP ...   
3    [[Flexible control of cognitive